# Access CMS LiDAR data
```{admonition} Learning Objectives
- Learn how to search files within a dataset programatically in Python
- Learn how to restrict search results by space (study area) and time (project period).
- Download data files of interest.
- Work with the data files.
```
In this tutorial, we will use `earthaccess` Python module to search for CMS datasets. 


In [1]:
import earthaccess
import numpy as np
import pandas as pd
import geopandas as gpd
import contextily as cx
import laspy
from shapely.geometry import box
from shapely.ops import orient

## LiDAR Surveys over Selected Forest Research Sites, Brazilian Amazon, 2008-2018

This dataset {cite:p}`dosSanos2019` provides the complete catalog of point cloud data collected during LiDAR surveys over selected forest research sites across the Amazon rainforest in Brazil between 2008 and 2018 for the Sustainable Landscapes Brazil Project. Flight lines were selected to overfly key field research sites in the Brazilian states of Acre, Amazonas, Bahia, Goias, Mato Grosso, Para, Rondonia, Santa Catarina, and Sao Paulo. The point clouds have been georeferenced, noise-filtered, and corrected for misalignment of overlapping flight lines. They are provided in 1 km x 1 km tiles. There are a total of 3,152 tiles in compressed [LAS (*.laz) file format](https://laszip.org/).

```{bibliography}
:style: plain
:filter: docname in docnames
```

We will use `earthaccess` module to search and download lidar data.

## Authentication

We recommend authenticating your [Earthdata Login (EDL)](https://urs.earthdata.nasa.gov) information using the earthaccess python library as follows:

In [2]:
# works if the EDL login already been persisted to a netrc
auth = earthaccess.login(strategy="netrc") 
if not auth.authenticated:
    # ask for EDL credentials and persist them in a .netrc file
    auth = earthaccess.login(strategy="interactive", persist=True)

## Search data granules
We will use `earthaccess`'s [search_data API](https://earthaccess.readthedocs.io/en/latest/user-reference/api/api/#earthaccess.api.search_data) to find the granules within the data collection.

In [3]:
granules = earthaccess.search_data(
    count=-1, # needed to retrieve all granules
    granule_name = '*.laz', # only find laz files
    doi="10.3334/ORNLDAAC/1644" # data collection doi
)
print(f"Total granules found: {len(granules)}")

Total granules found: 3152


Let's print the details of the first of the files.

In [4]:
granules[0]

Collection: {'ShortName': 'LiDAR_Forest_Inventory_Brazil_1644', 'Version': '1'}
Spatial coverage: {'HorizontalSpatialDomain': {'Geometry': {'BoundingRectangles': [{'WestBoundingCoordinate': -54.9676, 'EastBoundingCoordinate': -54.9527, 'NorthBoundingCoordinate': -3.00313, 'SouthBoundingCoordinate': -3.0176}]}}}
Temporal coverage: {'RangeDateTime': {'BeginningDateTime': '2008-01-01T00:00:00.000Z', 'EndingDateTime': '2008-12-31T23:59:59.000Z'}}
Size(MB): 90.198225
Data: ['https://data.ornldaac.earthdata.nasa.gov/protected/cms/LiDAR_Forest_Inventory_Brazil/data/TAP_A04_2008_laz_0.laz']

As we see above, the file is hosted in the NASA Earthdata Cloud.

The `granules` object contains metadata about the granules, including the bounding boxes, publication dates, data providers, etc. Now, let's convert the above granule metadata from json-formatted to `geopandas` dataframe. Converting to `geopandas` dataframe will let us easily generate various plots about the granules.

In [5]:
def convert_umm_bbox(b):
    """converts UMM bounding rectangles"""
    try:
        return box(b[0]['WestBoundingCoordinate'], 
              b[0]['SouthBoundingCoordinate'],
              b[0]['EastBoundingCoordinate'], 
              b[0]['NorthBoundingCoordinate'])
    except TypeError as e:
        return None

def convert_list_gdf(datag):
    """converts List[] to geopandas dataframe"""
    # create pandas dataframe from json
    df = pd.json_normalize([vars(granule)['render_dict'] for granule in datag])
    # keep only last string of the column names
    df.columns=df.columns.str.split('.').str[-1]
    df['geometry'] = df['BoundingRectangles'].apply(convert_umm_bbox)
    return gpd.GeoDataFrame(df, geometry="geometry", crs="EPSG:4326")
    
gdf = convert_list_gdf(granules)

## Plot granules bounding boxes
Let's now plot the bounding boxes for each granules. Here we only limit three columns for display purpose: `GranuleUR`, `size`, `geometry`.

In [6]:
gdf[['GranuleUR', 'size', 'geometry']].explore(color='red',  fillcolor='red')

## Region of Interest (ROI)
We will use a boundary of the [Reserva Florestal Adolpho Ducke](https://ppbio.inpa.gov.br/sitios/ducke) as the region of interest. Reserva Adolpho Ducke is a 10,000-hectare (25,000-acre) protected area of the Amazon rainforest on the outskirts of the city of Manaus, Brazil. It is a part of long term ecological research network and is one of the most intensively studied rainforest in the world.

Let's plot the study area over a base map.

In [7]:
poly = gpd.read_file("assets/reserva_ducke.json")
poly.explore(color='red',  fill=False)

## Search granules over ROI
We will use `earthaccess` python module to search for the granules overlapping the above ROI.

In [8]:
# bounding lon, lat as a list of tuples
poly.geometry = poly.geometry.apply(orient, args=(1,))
# simplifying the polygon to bypass the coordinates 
# limit of the CMR with a tolerance of .005 degrees
xy = poly.geometry.simplify(0.005).get_coordinates()

granules = earthaccess.search_data(
    count=-1, # needed to retrieve all granules
    granule_name = '*.laz', # only find laz files
    doi="10.3334/ORNLDAAC/1644", # dataset doi
    polygon=list(zip(xy.x, xy.y))
)
print(f"Total granules found: {len(granules)}")

Total granules found: 34


In [9]:
gdf = convert_list_gdf(granules)
gdf[['GranuleUR', 'size', 'geometry']].explore(color='red',  fillcolor='red')

## Download Datafiles

In [9]:
downloaded_files = earthaccess.download(granules, local_path="downloads")

QUEUEING TASKS | :   0%|          | 0/34 [00:00<?, ?it/s]

PROCESSING TASKS | :   0%|          | 0/34 [00:00<?, ?it/s]

COLLECTING RESULTS | :   0%|          | 0/34 [00:00<?, ?it/s]

In [10]:
downloaded_files

['downloads/DUC_A01_2008_laz_13.laz',
 'downloads/DUC_A01_2008_laz_1.laz',
 'downloads/DUC_A01_2008_laz_6.laz',
 'downloads/DUC_A01_2008_laz_12.laz',
 'downloads/DUC_A01_2008_laz_8.laz',
 'downloads/DUC_A01_2008_laz_5.laz',
 'downloads/DUC_A01_2008_laz_2.laz',
 'downloads/DUC_A01_2008_laz_9.laz',
 'downloads/DUC_A01_2008_laz_7.laz',
 'downloads/DUC_A01_2008_laz_0.laz',
 'downloads/DUC_A01_2008_laz_4.laz',
 'downloads/DUC_A01_2008_laz_10.laz',
 'downloads/DUC_A01_2008_laz_11.laz',
 'downloads/DUC_A01_2008_laz_3.laz',
 'downloads/DUC_A01_2017_LAS_16.laz',
 'downloads/DUC_A01_2017_LAS_11.laz',
 'downloads/DUC_A01_2017_LAS_2.laz',
 'downloads/DUC_A01_2017_LAS_14.laz',
 'downloads/DUC_A01_2017_LAS_5.laz',
 'downloads/DUC_A01_2017_LAS_4.laz',
 'downloads/DUC_A01_2017_LAS_1.laz',
 'downloads/DUC_A01_2017_LAS_3.laz',
 'downloads/DUC_A01_2017_LAS_6.laz',
 'downloads/DUC_A01_2017_LAS_18.laz',
 'downloads/DUC_A01_2017_LAS_19.laz',
 'downloads/DUC_A01_2017_LAS_10.laz',
 'downloads/DUC_A01_2017_LAS

In [12]:
point_cloud = laspy.read(downloaded_files[0])
print(point_cloud)

<LasData(1.0, point fmt: <PointFormat(1, 0 bytes of extra dims)>, 71736108 points, 0 vlrs)>


In [13]:
point_format = point_cloud.point_format
list(point_format.dimension_names)

['X',
 'Y',
 'Z',
 'intensity',
 'return_number',
 'number_of_returns',
 'scan_direction_flag',
 'edge_of_flight_line',
 'classification',
 'synthetic',
 'key_point',
 'withheld',
 'scan_angle_rank',
 'user_data',
 'point_source_id',
 'gps_time']